In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import classification_report
from sklearn.tree import  DecisionTreeClassifier

In [3]:
#ucitavanje skupa o perunikama
df = pd.read_csv("C:/Users/student/Desktop/ipIndustija4/vezbe7/iris.csv")

#izdvajanje skupa sa atributima za predvidjanje
featurs = df.columns[:4].tolist()
x=df[featurs]

#izdvajanje skupa sa ciljnim atributom
y=df["Species"]


In [4]:
# podela podataka na trening i test skup
#70% instanci ce biti u trening skupu, a 30% instanci u test skupu
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.3)


In [5]:
# vrednosti parametara klase DecisionTreeClassifier za unakrsnu validacuju
parameters = [{'criterion': ['gini', 'entropy'],
               'max_depth': [2, 3, 4, 5],
               'min_samples_split':[15, 10, 15],
               'min_samples_leaf': [2, 4, 6]
               }]

#za svaki parametar se zadaje lista vrednosti (napomena: ako se zadaje samo
# jedna vrednost za neki parametar, mora se zadati kao element liste, npr.
# 'criterion': ['gini'])

# moguce je praviti i vise recnika u okviru liste, npr.
# [{'criterion': ['gini', 'entropy'],
#                'min_samples_split':[15, 10, 15]} ,
# {               'min_samples_leaf': [2, 4, 6],
#                'max_depth': [2, 3, 4, 5],
#                }]
# tada ce se praviti modeli na osnovu kombinacija za parametre zadate
# u prvom recnika, a zatim modeli na osnovu kombinacija za parametre
# zadate u drugom recniku


In [8]:
clf = GridSearchCV(DecisionTreeClassifier(), parameters, cv=5)

#pravi se model sa optimalnim vrednostima za parametre
#Bitno: sa GridSearchCV(...) se pronalaze najbolje vrednosti medju zadatim za parametre,
#a pozivom fit(x,y) se pravi model sa najboljim vrednostima za parametre koriscenjem
#svih instanci trening skupa
    
clf.fit(x_train, y_train)




GridSearchCV(cv=5, estimator=DecisionTreeClassifier(),
             param_grid=[{'criterion': ['gini', 'entropy'],
                          'max_depth': [2, 3, 4, 5],
                          'min_samples_leaf': [2, 4, 6],
                          'min_samples_split': [15, 10, 15]}])

In [9]:
clf.best_params_

{'criterion': 'entropy',
 'max_depth': 3,
 'min_samples_leaf': 2,
 'min_samples_split': 15}

In [11]:
print("Ocena uspeha po klasifikatorima:")
    
means = clf.cv_results_['mean_test_score']  # za svaku koriscenu kombinaciju
                                            # vrednosti za parametre dobija se
                                            # srednja vrednost mere za ocenu modela dobijena
                                            # na osnovu k test delova

stds = clf.cv_results_['std_test_score']    # za svaku koriscenu kombinaciju
                                            # vrednosti za parametre dobija se
                                            # standardna devijacija vrednosti mere
                                            # za ocenu modela dobijena
                                            # na osnovu k test delova

#za svaku koriscenu kombinaciju vrednosti za parametre se izdvaja izvestaj
# (srednja vrednost mere za ocenu modela +/- 2 standardne devijacije)
for mean, std, params in zip(means, stds, clf.cv_results_['params']):
    print("%0.3f (+/-%0.03f) za %s" % (mean, std * 2, params))
print()


Ocena uspeha po klasifikatorima:
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 2, 'min_samples_split': 15}
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 2, 'min_samples_split': 10}
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 2, 'min_samples_split': 15}
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 4, 'min_samples_split': 15}
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 4, 'min_samples_split': 10}
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 4, 'min_samples_split': 15}
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 6, 'min_samples_split': 15}
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 6, 'min_samples_split': 10}
0.914 (+/-0.093) za {'criterion': 'gini', 'max_depth': 2, 'min_samples_leaf': 6, 'min_samples_split': 15}
0.952 (+/-0.0

In [12]:
# model napravljen koriscenjem najboljih parametara se
# primenjuje na test skup i izdvaja izvestaj o klasifikaciji
# (krajnja ocena modela)
print("Izvestaj za test skup:")
y_true, y_pred = y_test, clf.predict(x_test)
print(classification_report(y_true, y_pred))
print()


Izvestaj za test skup:
              precision    recall  f1-score   support

      setosa       1.00      1.00      1.00         9
  versicolor       1.00      0.95      0.97        20
   virginica       0.94      1.00      0.97        16

    accuracy                           0.98        45
   macro avg       0.98      0.98      0.98        45
weighted avg       0.98      0.98      0.98        45




In [13]:
# promena mere za ocenu modela koje ce se korstiti u unakrsnoj validaciji
scores = ['precision', 'f1']

for score in scores:
    print("Mera ", score)

    clf = GridSearchCV(DecisionTreeClassifier(), parameters, cv=5, scoring='%s_macro' % score)
    clf.fit(x_train, y_train)

    print("Izvestaj za test skup:")
    y_true, y_pred = y_test, clf.predict(x_test)
    print(classification_report(y_true, y_pred))
    print()


Mera  precision
Izvestaj za test skup:
              precision    recall  f1-score   support

      setosa       1.00      1.00      1.00         9
  versicolor       1.00      0.95      0.97        20
   virginica       0.94      1.00      0.97        16

    accuracy                           0.98        45
   macro avg       0.98      0.98      0.98        45
weighted avg       0.98      0.98      0.98        45


Mera  f1
Izvestaj za test skup:
              precision    recall  f1-score   support

      setosa       1.00      1.00      1.00         9
  versicolor       1.00      0.95      0.97        20
   virginica       0.94      1.00      0.97        16

    accuracy                           0.98        45
   macro avg       0.98      0.98      0.98        45
weighted avg       0.98      0.98      0.98        45


